In [3]:
import jax
import optax
import flax
import jax.numpy as jnp
import datasets
from flax.training import train_state
from flax.training.common_utils import get_metrics, onehot, shard
from datasets import load_dataset
from tokenizers import trainers, Tokenizer, normalizers, ByteLevelBPETokenizer
from pathlib import Path
import numpy as np
import transformers
from tqdm.notebook import tqdm
from pathlib import Path
from transformers import AutoConfig
from typing import Dict, List, Optional, Tuple
from transformers import AutoTokenizer
from transformers import PreTrainedTokenizerBase
from transformers import FlaxAutoModelForMaskedLM
from dataclasses import dataclass, field
import time
import glob
import random

In [11]:
#59G c4_cleaned compressed
#937M nrc_uniq_cleaned_20210223 compressed
#410M nu_uniq_cleaned_20210225 compressed
#9.9G oscar_nl_cleaned compressed



data_files = []
SEED=42
def add_jsonlines_dir(path):
    global data_files
    #data_files += glob.glob(f"{path}/*47*.gz")
    #data_files += glob.glob(f"{path}/*32*.gz")
    #data_files += glob.glob(f"{path}/*59*.gz")
    data_files += glob.glob(f"{path}/*11*.gz")
    print(f"Number of files {len(data_files)} after adding {path}")
    
add_jsonlines_dir("/data/c4_cleaned")
#add_jsonlines_dir("/data/nrc_uniq_cleaned_20210223")
#add_jsonlines_dir("/data/nu_uniq_cleaned_20210225")
#add_jsonlines_dir("/data/oscar_nl_cleaned") This one gives an error like field url not in 



Number of files 20 after adding /data/c4_cleaned


In [5]:
#59G c4_cleaned compressed
#937M nrc_uniq_cleaned_20210223 compressed
#410M nu_uniq_cleaned_20210225 compressed
#9.9G oscar_nl_cleaned compressed



data_files = []
SEED=42
def add_jsonlines_dir(path,filespec):
    global data_files
    data_files += glob.glob(f"{path}/{filespec}")
    print(f"Number of files {len(data_files)} after adding {path}")
    
add_jsonlines_dir("/home/dat/subset_c4_cleannl","*.gz")   
#add_jsonlines_dir("/data/oscar_nl_cleaned","*.gz")
#add_jsonlines_dir("/data/nrc_cleaned_idtextfmt","*.gz")
#add_jsonlines_dir("/data/nu_cleaned_idtextfmt","*.gz")
random.Random(SEED).shuffle(data_files)
total = len(data_files)
val_size = int(0.05 * total)
train_size = total - val_size
print(f"95%: {train_size}")
train = data_files[:train_size]
val = data_files[train_size:]
print(f"Got {len(train)} training files and {len(val)} validation files")
assert list(set(train) & set(val)) == [], "Train overlaps with test"
datasets = load_dataset('json', data_files={'train': train, 'validation': val})


assert list(set(train) & set(val)) == [], 'train overlaps with test'


Number of files 3 after adding /home/dat/subset_c4_cleannl
Got 3 training files and 3 validation files


AssertionError: Train overlaps with test

In [ ]:

            add_jsonlines_dir("/home/dat/subset_c4_cleannl")   
            add_jsonlines_dir("/data/oscar_nl_cleaned")
            add_jsonlines_dir("/data/nrc_cleaned_idtextfmt")
            add_jsonlines_dir("/data/nu_cleaned_idtextfmt")
            random.Random(SEED).shuffle(data_files)
            total = len(data_files)
            val_size = int(0.05 * total)
            train_size = total - val_size
            print(f"95%: {train_size}")
            train = data_files
            val = data_files
            print(f"Got {len(train)} training files and {len(val)} validation files")
            assert list(set(train) & set(val)) == [], "Train overlaps with test"
            return train, val
        train, val = train_val_files()
        datasets = load_dataset('json', data_files={'train': train, 'validation': val})

In [4]:
from tokenizers import ByteLevelBPETokenizer
tokenizer = ByteLevelBPETokenizer()

def batch_iterator(batch_size=1000):
    for i in range(0, len(datasets), batch_size):
        yield datasets["train"][i: i + batch_size]["text"]

tokenizer.train_from_iterator(batch_iterator(), vocab_size=50358, min_frequency=2, special_tokens=[
    "<s>",
    "<pad>",
    "</s>",
    "<unk>",
    "<mask>",
])

In [5]:
tokenizer.get_vocab_size()

39503

In [6]:
cd ~/pino-roberta-base

/home/dat/pino-roberta-base


In [7]:
tokenizer.save("tokenizer.json")

In [ ]:
dataset1 = load_dataset("mc4", "nl", streaming=True)
dataset2 = load_dataset("oscar", "unshuffled_deduplicated_nl",streaming=True)
dataset3 = load_dataset("cc100", lang="nl")



Using custom data configuration nl-lang=nl


Downloading:   0%|          | 0.00/8.42G [00:00<?, ?B/s]

In [14]:
from transformers import AutoTokenizer, RobertaModel
from transformers import BigBirdForSequenceClassification,FlaxBigBirdModel,FlaxBigBirdForMaskedLM

model = FlaxBigBirdModel.from_pretrained("flax-community/pino-roberta-base")
model.save_pretrained('exported_pytorch_model')

INFO:absl:Starting the local TPU driver.
INFO:absl:Unable to initialize backend 'tpu_driver': Not found: Unable to find driver in registry given worker: local://
INFO:absl:Unable to initialize backend 'gpu': Not found: Could not find registered platform with name: "cuda". Available platform names are: Interpreter Host TPU
Some weights of FlaxBigBirdModel were not initialized from the model checkpoint at flax-community/pino-roberta-base and are newly initialized: {('pooler', 'kernel'), ('pooler', 'bias')}
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
